In [1]:
import requests
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from bs4 import BeautifulSoup as BS
from lxml import html
import re
import difflib
from functools import partial
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [2]:
pip install fuzzywuzzy

Note: you may need to restart the kernel to use updated packages.


In [3]:
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

C:\Users\rober\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [4]:
imdbdf = pd.read_csv("../data/imdbdf.csv")

In [5]:
imdbdf = imdbdf.drop("Unnamed: 0",axis=1)

In [6]:
imdbdf.loc[(imdbdf['Title'] == 'SMILE')]

Title  Release Year     Rating  Runtime IMDB Score     Metascore
3     SMILE        2022.0          R    115.0        6.6            68
1006  SMILE        2009.0  Not Rated     84.0        3.3  NO METASCORE
1698  SMILE        2022.0  NO RATING      NaN        3.8  NO METASCORE

In [7]:
imdbdf = imdbdf.drop(1698)

In [8]:
imdbdf.loc[(imdbdf['Title'] == 'SMILE')]

Title  Release Year     Rating  Runtime IMDB Score     Metascore
3     SMILE        2022.0          R    115.0        6.6            68
1006  SMILE        2009.0  Not Rated     84.0        3.3  NO METASCORE

In [9]:
imdbdf['Release Year'] = pd.to_numeric(imdbdf['Release Year'])
imdbdf.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9999 entries, 0 to 9999
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Title         9999 non-null   object 
 1   Release Year  9607 non-null   float64
 2   Rating        9999 non-null   object 
 3   Runtime       9234 non-null   float64
 4   IMDB Score    9999 non-null   object 
 5   Metascore     9999 non-null   object 
dtypes: float64(2), object(4)
memory usage: 546.8+ KB


In [10]:
imdbdf = imdbdf[imdbdf['Release Year'].notna()]

In [11]:
imdbdf.index = np.arange(1, len(imdbdf) + 1)
imdbdf['Title'] = imdbdf['Title'].str.upper()

In [12]:
imdbdf['Title'] = imdbdf['Title'].fillna(value=1408)

In [13]:
imdbdf.head(300)

Title  Release Year     Rating  Runtime      IMDB Score     Metascore
1                                             THE MENU        2022.0          R    107.0             7.5            71
2                                                    X        2022.0          R    105.0             6.6            79
3                                        BONES AND ALL        2022.0          R    131.0             7.3            74
4                                                SMILE        2022.0          R    115.0             6.6            68
5                                            BARBARIAN        2022.0          R    102.0             7.1            78
6                                              BHEDIYA        2022.0  NO RATING    156.0             7.7  NO METASCORE
7                                                 NOPE        2022.0          R    130.0             6.9            77
8                                         THE MEAN ONE        2022.0  NO RATING     93.0             6.3            32
9                                          TERRIFIER 2        2022.0  Not Rated    138.0             6.3            59
10                                               PEARL        2022.0          R    103.0             7.0            73
11                                              SCREAM        2022.0          R    114.0             6.3            60
12                                         WHITE NOISE        2022.0          R    136.0             6.6            67
13                               SOMETHING IN THE DIRT        2022.0          R    116.0             6.0            76
14                        THE BABYSITTER: KILLER QUEEN        2020.0      TV-MA    101.0             5.8            22
15                                         SKINAMARINK        2022.0  NO RATING    100.0             5.5  NO METASCORE
16                                   THE ADDAMS FAMILY        2019.0         PG     86.0             5.8            46
17                                           TERRIFIER        2016.0    Unrated     85.0             5.6  NO METASCORE
18                    WINNIE-THE-POOH: BLOOD AND HONEY        2023.0  NO RATING      NaN  NO IMDB RATING  NO METASCORE
19                                           MIDSOMMAR        2019.0          R    148.0             7.1            72
20                                            SCREAM 6        2023.0  NO RATING      NaN  NO IMDB RATING  NO METASCORE
21                                     AMERICAN PSYCHO        2000.0          R    102.0             7.6            64
22                                BODIES BODIES BODIES        2022.0          R     94.0             6.3            69
23                                             GET OUT        2017.0          R    104.0             7.7            85
24         DOCTOR STRANGE IN THE MULTIVERSE OF MADNESS        2022.0      PG-13    126.0             6.9            60
25                                                TUSK        2014.0          R    102.0             5.3            55
26                                  LAST NIGHT IN SOHO        2021.0          R    116.0             7.1            65
27                                     THE BLACK PHONE        2021.0          R    103.0             6.9            65
28                                                PREY        2022.0          R    100.0             7.2            71
29                                  KNOCK AT THE CABIN        2023.0          R      NaN  NO IMDB RATING  NO METASCORE
30                                             KRAMPUS        2015.0      PG-13     98.0             6.2            49
31                                               ALIEN        1979.0          R    117.0             8.5            89
32                                CRIMES OF THE FUTURE        2022.0          R    107.0             5.9            67
33                                             MORBIUS        2022.0      PG-13    104.0             5.2            35
34 

In [14]:
wwbo = pd.read_excel("../data/thenumbers.xlsx", sheet_name=('All Time Worldwide Box Office'))
wwbo.index = np.arange(1, len(wwbo) + 1)
wwbo = wwbo.rename(columns={'Movie' : 'Title', 'Released' : 'Release Year'})
wwbo['Worldwide']=wwbo['Worldwide'].apply('{:,}'.format)
wwbo['Domestic']=wwbo['Domestic'].apply('{:,}'.format)
wwbo['International']=wwbo['International'].apply('{:,}'.format)

In [15]:
wwbo['Title'] = wwbo['Title'].str.upper()

In [16]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International
1             2017                                    IT  701,012,746  328,828,874.0  372,183,872.0
2             1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0
3             2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0
4             1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0
5             2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0
...            ...                                   ...          ...            ...            ...
1851          2018                          MANIAC TALES          155            nan          155.0
1852          1933                     THE INVISIBLE MAN          132            nan          132.0
1853          2016                  CAPTURE KILL RELEASE           72            nan           72.0
1854          2021                SLUMBER PARTY MASSACRE           28            nan           28.0
1855          2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0

[1855 rows x 5 columns]

In [17]:
#df[['a', 'b']] = df[['a','b']].fillna(value=0)

wwbo['Title'] = wwbo['Title'].fillna(value=1408)

In [18]:
wwbo.head(100)

Release Year                                     Title    Worldwide       Domestic  International
1            2017                                        IT  701,012,746  328,828,874.0  372,183,872.0
2            1975                                      JAWS  482,947,378  272,257,035.0  210,690,343.0
3            2007                               I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0
4            1973                              THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0
5            2019                           IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0
6            2018                             A QUIET PLACE  334,876,670  188,024,361.0  146,852,309.0
7            2017                                   GET OUT  252,297,405  175,837,935.0   76,459,470.0
8            2001                                  HANNIBAL  350,100,280  165,092,266.0  185,008,014.0
9            2021                    A QUIET PLACE: PART II  296,650,356  160,215,764.0  136,434,592.0
10           2018                                 HALLOWEEN  255,416,089  159,366,015.0   96,050,074.0
11           1999                   THE BLAIR WITCH PROJECT  248,300,000  140,539,099.0  107,760,901.0
12           2017                                     SPLIT  278,754,594  138,141,585.0  140,613,009.0
13           2013                             THE CONJURING  317,740,900  137,400,141.0  180,340,759.0
14           1991                  THE SILENCE OF THE LAMBS  275,726,716  130,726,716.0  145,000,000.0
15           2002                                  THE RING  248,218,486  129,094,024.0  119,124,462.0
16           2022                                      NOPE  171,416,477  123,277,080.0   48,139,397.0
17           2018                                   THE NUN  363,391,647  117,450,119.0  245,941,528.0
18           2004                                THE GRUDGE  187,281,115  110,359,362.0   76,921,753.0
19           2009                       PARANORMAL ACTIVITY  194,183,034  107,918,810.0   86,264,224.0
20           2022                                     SMILE  215,978,513  105,778,513.0  110,200,000.0
21           1994                INTERVIEW WITH THE VAMPIRE  223,564,608  105,264,608.0  118,300,000.0
22           2011                     PARANORMAL ACTIVITY 3  207,039,844  104,028,807.0  103,011,037.0
23           1996                                    SCREAM  173,046,640  103,046,663.0   69,999,977.0
24           1978                                    JAWS 2  208,900,376  102,922,376.0  105,978,000.0
25           2016  THE CONJURING 2: THE ENFIELD POLTERGEIST  310,196,332  102,470,008.0  207,726,324.0
26           2017                       ANNABELLE: CREATION  305,384,865  102,092,201.0  203,292,664.0
27           1997                                  SCREAM 2  172,363,301  101,363,301.0   71,000,000.0
28           1999                             SLEEPY HOLLOW  207,068,340  101,068,340.0  106,000,000.0
29           2001                                THE OTHERS  207,765,056   96,522,687.0  111,242,369.0
30           2021                           HALLOWEEN KILLS  130,851,162   92,002,155.0   38,849,007.0
31           1999                              THE HAUNTING  180,188,905   91,188,905.0   89,000,000.0
32           2022                           THE BLACK PHONE  161,204,799   89,887,230.0   71,317,569.0
33           2016                             DON’T BREATHE  158,906,350   89,217,875.0   69,688,475.0
34           2000                                  SCREAM 3  161,838,076   89,138,076.0   72,700,000.0
35           2005                                    SAW II  152,925,093   87,025,093.0   65,900,000.0
36           1979                     THE AMITYVILLE HORROR   86,432,520   86,432,520.0            nan
37           2010                     PARANORMAL ACTIVITY 2  177,512,032   84,752,907.0   92,759,125.0
38           2014                                 ANNABELLE  256,857,527   84,273,813.0  17

In [19]:
tdbo = pd.read_excel("../data/thenumbers.xlsx", sheet_name=('Top 100 Domestic Box Office'))
tdbo.index = np.arange(1, len(tdbo) + 1)
tdbo = tdbo.rename(columns={'Movie' : 'Title', 'Released' : 'Release Year', 'Infl. Adj. Dom.' : 'Domestic - Adjusted for Inflation'})
tdbo['Domestic']=tdbo['Domestic'].apply('{:,}'.format)
tdbo['Domestic - Adjusted for Inflation']=tdbo['Domestic - Adjusted for Inflation'].apply('{:,}'.format)
tdbo['Title'] = tdbo['Title'].str.upper()

In [20]:
tdbo['Title'] = tdbo['Title'].fillna(value=1408)

In [21]:
tdbo

Release Year                                              Title     Domestic Domestic - Adjusted for Inflation
1            2017                                                 IT  328,828,874                       334,783,459
2            1973                                       THE EXORCIST  230,347,346                     1,063,304,892
3            2019                                     IT CHAPTER TWO  211,593,228                       211,824,221
4            2018                                      A QUIET PLACE  188,024,361                       189,262,720
5            2017                                            GET OUT  175,837,935                       179,752,944
6            2020                              A QUIET PLACE PART II  160,215,764                       160,215,764
7            2018                                          HALLOWEEN  159,366,015                       160,409,948
8            1999                            THE BLAIR WITCH PROJECT  140,539,099                       253,689,664
9            2016                                              SPLIT  138,141,585                       141,221,659
10           2013                                      THE CONJURING  137,400,141                       154,976,540
11           2002                                           THE RING  129,094,024                       203,643,481
12           2022                                               NOPE  123,277,080                       123,277,080
13           2018                                            THE NUN  117,450,119                       118,223,666
14           2004                                         THE GRUDGE  110,359,362                       162,962,207
15           2007                                PARANORMAL ACTIVITY  107,918,810                       131,944,856
16           2022                                              SMILE  105,778,513                       105,778,513
17           1994  INTERVIEW WITH THE VAMPIRE: THE VAMPIRE CHRONI...  105,264,608                       235,963,201
18           2011                              PARANORMAL ACTIVITY 3  104,028,807                       120,295,508
19           1996                                             SCREAM  103,046,663                       208,875,525
20           2016                                    THE CONJURING 2  102,470,008                       108,630,057
21           2017                                ANNABELLE: CREATION  102,092,201                       104,368,502
22           1997                                           SCREAM 2  101,363,301                       201,830,911
23           1999                                      SLEEPY HOLLOW  101,068,340                       181,585,991
24           2001                                         THE OTHERS   96,522,687                       156,380,393
25           2021                                    HALLOWEEN KILLS   92,002,155                        92,002,155
26           1999                                       THE HAUNTING   91,188,905                       164,606,736
27           2021                                    THE BLACK PHONE   89,887,230                        89,887,230
28           2016                                      DON'T BREATHE   89,217,875                        94,581,260
29           2000                                           SCREAM 3   89,138,076                       151,650,489
30           2005                                             SAW II   87,025,093                       124,495,771
31           1979                              THE AMITYVILLE HORROR   86,432,520                       315,771,389
32           2010                              PARANORMAL ACTIVITY 2   84,752,907                        98,501,884
33           2014                                          ANNABELLE   84,273,813                        94,588,843
34           2013                               INSIDIOUS: CH

In [22]:
top100comb = pd.merge(tdbo, imdbdf, left_on = ['Title', 'Release Year'], right_on = ['Title', 'Release Year'], how='left')
top100comb.index = np.arange(1, len(top100comb) + 1)

In [23]:
top100comb

Release Year                                              Title     Domestic Domestic - Adjusted for Inflation Rating  Runtime IMDB Score     Metascore
1            2017                                                 IT  328,828,874                       334,783,459      R    135.0        7.3            69
2            1973                                       THE EXORCIST  230,347,346                     1,063,304,892      R    122.0        8.1            81
3            2019                                     IT CHAPTER TWO  211,593,228                       211,824,221      R    169.0        6.5            58
4            2018                                      A QUIET PLACE  188,024,361                       189,262,720  PG-13     90.0        7.5            82
5            2017                                            GET OUT  175,837,935                       179,752,944      R    104.0        7.7            85
6            2020                              A QUIET PLACE PART II  160,215,764                       160,215,764  PG-13     97.0        7.2            71
7            2018                                          HALLOWEEN  159,366,015                       160,409,948      R    106.0        6.5            67
8            1999                            THE BLAIR WITCH PROJECT  140,539,099                       253,689,664      R     81.0        6.5            81
9            2016                                              SPLIT  138,141,585                       141,221,659  PG-13    117.0        7.3            62
10           2013                                      THE CONJURING  137,400,141                       154,976,540      R    112.0        7.5            68
11           2002                                           THE RING  129,094,024                       203,643,481  PG-13    115.0        7.1            57
12           2022                                               NOPE  123,277,080                       123,277,080      R    130.0        6.9            77
13           2018                                            THE NUN  117,450,119                       118,223,666      R     96.0        5.3            46
14           2004                                         THE GRUDGE  110,359,362                       162,962,207  PG-13     91.0        5.9            49
15           2007                                PARANORMAL ACTIVITY  107,918,810                       131,944,856      R     86.0        6.3            68
16           2022                                              SMILE  105,778,513                       105,778,513      R    115.0        6.6            68
17           1994  INTERVIEW WITH THE VAMPIRE: THE VAMPIRE CHRONI...  105,264,608                       235,963,201      R    123.0        7.5            59
18           2011                              PARANORMAL ACTIVITY 3  104,028,807                       120,295,508      R     83.0        5.8            59
19           1996                                             SCREAM  103,046,663                       208,875,525      R    111.0        7.4            65
20           2016                                    THE CONJURING 2  102,470,008                       108,630,057      R    134.0        7.3            65
21           2017                                ANNABELLE: CREATION  102,092,201                       104,368,502      R    109.0        6.5            62
22           1997                                           SCREAM 2  101,363,301                       201,830,911      R    120.0        6.3            63
23           1999                                      SLEEPY HOLLOW  101,068,340                       181,585,991      R    105.0        7.3            65
24           2001                                         THE OTHERS   96,522,687                       156,380,393  PG-13    104.0        7.6            74
25           2021                                    HALLOWEEN KILLS   92,002,15

In [24]:
imdbdf['Release Year'] = imdbdf['Release Year'].astype(str)

In [25]:
imdbdf.dtypes

Title            object
Release Year     object
Rating           object
Runtime         float64
IMDB Score       object
Metascore        object
dtype: object

In [26]:
imdbdf['Title and Year'] = imdbdf['Title'] + " " + imdbdf['Release Year']

In [27]:
imdbdf.head()

Title Release Year Rating  Runtime IMDB Score Metascore        Title and Year
1       THE MENU       2022.0      R    107.0        7.5        71       THE MENU 2022.0
2              X       2022.0      R    105.0        6.6        79              X 2022.0
3  BONES AND ALL       2022.0      R    131.0        7.3        74  BONES AND ALL 2022.0
4          SMILE       2022.0      R    115.0        6.6        68          SMILE 2022.0
5      BARBARIAN       2022.0      R    102.0        7.1        78      BARBARIAN 2022.0

In [28]:
wwbo['Release Year'] = wwbo['Release Year'].astype(str)

In [29]:
wwbo['Title'] = wwbo['Title'].astype(str)

In [30]:
wwbo['Title and Year'] = wwbo['Title'] + " " + wwbo['Release Year']

In [31]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International                             Title and Year
1            2017                                    IT  701,012,746  328,828,874.0  372,183,872.0                                    IT 2017
2            1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0                                  JAWS 1975
3            2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                           I AM LEGEND 2007
4            1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                          THE EXORCIST 1973
5            2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                       IT: CHAPTER TWO 2019
...           ...                                   ...          ...            ...            ...                                        ...
1851         2018                          MANIAC TALES          155            nan          155.0                          MANIAC TALES 2018
1852         1933                     THE INVISIBLE MAN          132            nan          132.0                     THE INVISIBLE MAN 1933
1853         2016                  CAPTURE KILL RELEASE           72            nan           72.0                  CAPTURE KILL RELEASE 2016
1854         2021                SLUMBER PARTY MASSACRE           28            nan           28.0                SLUMBER PARTY MASSACRE 2021
1855         2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0  ANTRUM: THE DEADLIEST FILM EVER MADE 2019

[1855 rows x 6 columns]

In [32]:
wwbo.dtypes

Release Year      object
Title             object
Worldwide         object
Domestic          object
International     object
Title and Year    object
dtype: object

In [33]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International                             Title and Year
1            2017                                    IT  701,012,746  328,828,874.0  372,183,872.0                                    IT 2017
2            1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0                                  JAWS 1975
3            2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                           I AM LEGEND 2007
4            1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                          THE EXORCIST 1973
5            2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                       IT: CHAPTER TWO 2019
...           ...                                   ...          ...            ...            ...                                        ...
1851         2018                          MANIAC TALES          155            nan          155.0                          MANIAC TALES 2018
1852         1933                     THE INVISIBLE MAN          132            nan          132.0                     THE INVISIBLE MAN 1933
1853         2016                  CAPTURE KILL RELEASE           72            nan           72.0                  CAPTURE KILL RELEASE 2016
1854         2021                SLUMBER PARTY MASSACRE           28            nan           28.0                SLUMBER PARTY MASSACRE 2021
1855         2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0  ANTRUM: THE DEADLIEST FILM EVER MADE 2019

[1855 rows x 6 columns]

In [34]:
wwbo.to_csv('wwbo.csv')

In [35]:
imdbdf.dtypes

Title              object
Release Year       object
Rating             object
Runtime           float64
IMDB Score         object
Metascore          object
Title and Year     object
dtype: object

In [36]:
imdbdf['Runtime'] = imdbdf['Runtime'].astype(str)

In [37]:
imdbdf

Title Release Year     Rating Runtime      IMDB Score     Metascore                     Title and Year
1                       THE MENU       2022.0          R   107.0             7.5            71                    THE MENU 2022.0
2                              X       2022.0          R   105.0             6.6            79                           X 2022.0
3                  BONES AND ALL       2022.0          R   131.0             7.3            74               BONES AND ALL 2022.0
4                          SMILE       2022.0          R   115.0             6.6            68                       SMILE 2022.0
5                      BARBARIAN       2022.0          R   102.0             7.1            78                   BARBARIAN 2022.0
...                          ...          ...        ...     ...             ...           ...                                ...
9603       WALKING DEAD - TOMATE       2022.0  NO RATING    79.0             3.6  NO METASCORE       WALKING DEAD - TOMATE 2022.0
9604                   MANNEQUIN       2023.0  NO RATING     nan  NO IMDB RATING  NO METASCORE                   MANNEQUIN 2023.0
9605  UNDEAD OR ALIVE: A ZOMBEDY       2007.0          R    91.0             5.1  NO METASCORE  UNDEAD OR ALIVE: A ZOMBEDY 2007.0
9606               SECOND ORIGIN       2015.0  NO RATING   106.0             4.5  NO METASCORE               SECOND ORIGIN 2015.0
9607                       BETSY       2018.0  NO RATING    81.0             3.1  NO METASCORE                       BETSY 2018.0

[9607 rows x 7 columns]

In [38]:
imdbdf.loc[(imdbdf['Title'] == '1408')]

Title Release Year Rating Runtime IMDB Score Metascore Title and Year
325  1408       2007.0  PG-13   104.0        6.8        64    1408 2007.0

In [39]:
wwbo.loc[(wwbo['Title'] == '1408')]

Release Year Title    Worldwide      Domestic International Title and Year
55           2007  1408  131,263,370  71,985,628.0  59,277,742.0      1408 2007
594          2016  1408      922,727     779,820.0     142,907.0      1408 2016
744          2011  1408    2,756,875      38,100.0   2,718,775.0      1408 2011
959          2018  1408    3,130,260           nan   3,130,260.0      1408 2018
1347         2020  1408      123,784           nan     123,784.0      1408 2020

In [40]:
#imdbdf = imdbdf.drop(1698) drop extra 1408

In [41]:
wwbo = wwbo.drop(594)
wwbo = wwbo.drop(744)
wwbo = wwbo.drop(959)
wwbo = wwbo.drop(1347)

In [42]:
wwbo.loc[(wwbo['Title'] == '1408')]

Release Year Title    Worldwide      Domestic International Title and Year
55         2007  1408  131,263,370  71,985,628.0  59,277,742.0      1408 2007

In [43]:
wwbo.head()

Release Year            Title    Worldwide       Domestic  International        Title and Year
1         2017               IT  701,012,746  328,828,874.0  372,183,872.0               IT 2017
2         1975             JAWS  482,947,378  272,257,035.0  210,690,343.0             JAWS 1975
3         2007      I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0      I AM LEGEND 2007
4         1973     THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0     THE EXORCIST 1973
5         2019  IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0  IT: CHAPTER TWO 2019

In [44]:
wwbo.shape

(1851, 6)

In [45]:
imdbdf.head()

Title Release Year Rating Runtime IMDB Score Metascore        Title and Year
1       THE MENU       2022.0      R   107.0        7.5        71       THE MENU 2022.0
2              X       2022.0      R   105.0        6.6        79              X 2022.0
3  BONES AND ALL       2022.0      R   131.0        7.3        74  BONES AND ALL 2022.0
4          SMILE       2022.0      R   115.0        6.6        68          SMILE 2022.0
5      BARBARIAN       2022.0      R   102.0        7.1        78      BARBARIAN 2022.0

In [46]:
imdbdf.shape

(9607, 7)

In [47]:
# title a / title b / calc ratio of similarity - abi's suggestion

#df['candidate'] = get_close_matches()

In [48]:
# worldwidecomb = pd.merge(imdbdf, wwbo, left_on = ['Title', 'Release Year'], right_on = ['Title', 'Release Year'], how='inner')
# worldwidecomb.index = np.arange(1, len(top100comb) + 1)

# df2['team'] = df2['team'].apply(lambda x: difflib.get_close_matches(x, df1['team'])[0])

#wwbo['Title and Year'] = wwbo['Title and Year'].map(lambda x: difflib.get_close_matches(x, imdbdf['Title and Year'])[0])

#test = imdbdf.merge(wwbo)

#df2.index = df2.index.map(lambda x: difflib.get_close_matches(x, df1.index)[0])

# for x in wwbo['Title and Year']:
#     wwbo['Match'] = difflib.get_close_matches(x, imdbdf['Title and Year'])[0]
#     print(x)
#     print(difflib.get_close_matches(x, imdbdf['Title and Year'])[0])

In [49]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International                             Title and Year
1            2017                                    IT  701,012,746  328,828,874.0  372,183,872.0                                    IT 2017
2            1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0                                  JAWS 1975
3            2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                           I AM LEGEND 2007
4            1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                          THE EXORCIST 1973
5            2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                       IT: CHAPTER TWO 2019
...           ...                                   ...          ...            ...            ...                                        ...
1851         2018                          MANIAC TALES          155            nan          155.0                          MANIAC TALES 2018
1852         1933                     THE INVISIBLE MAN          132            nan          132.0                     THE INVISIBLE MAN 1933
1853         2016                  CAPTURE KILL RELEASE           72            nan           72.0                  CAPTURE KILL RELEASE 2016
1854         2021                SLUMBER PARTY MASSACRE           28            nan           28.0                SLUMBER PARTY MASSACRE 2021
1855         2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0  ANTRUM: THE DEADLIEST FILM EVER MADE 2019

[1851 rows x 6 columns]

In [50]:
#df.to_csv('file1.csv')

In [51]:
wwbo.to_csv('wwbo.csv')

In [52]:
imdbdf.to_csv('imdbdf.csv')

In [53]:
wwbo['match'] = wwbo['Title'].str[0:8]

In [54]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International                             Title and Year     match
1            2017                                    IT  701,012,746  328,828,874.0  372,183,872.0                                    IT 2017        IT
2            1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0                                  JAWS 1975      JAWS
3            2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                           I AM LEGEND 2007  I AM LEG
4            1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                          THE EXORCIST 1973  THE EXOR
5            2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                       IT: CHAPTER TWO 2019  IT: CHAP
...           ...                                   ...          ...            ...            ...                                        ...       ...
1851         2018                          MANIAC TALES          155            nan          155.0                          MANIAC TALES 2018  MANIAC T
1852         1933                     THE INVISIBLE MAN          132            nan          132.0                     THE INVISIBLE MAN 1933  THE INVI
1853         2016                  CAPTURE KILL RELEASE           72            nan           72.0                  CAPTURE KILL RELEASE 2016  CAPTURE 
1854         2021                SLUMBER PARTY MASSACRE           28            nan           28.0                SLUMBER PARTY MASSACRE 2021  SLUMBER 
1855         2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0  ANTRUM: THE DEADLIEST FILM EVER MADE 2019  ANTRUM: 

[1851 rows x 7 columns]

In [55]:
imdbdf['match'] = imdbdf['Title and Year'].str[0:8]

In [56]:
imdbdf.head()

Title Release Year Rating Runtime IMDB Score Metascore        Title and Year     match
1       THE MENU       2022.0      R   107.0        7.5        71       THE MENU 2022.0  THE MENU
2              X       2022.0      R   105.0        6.6        79              X 2022.0  X 2022.0
3  BONES AND ALL       2022.0      R   131.0        7.3        74  BONES AND ALL 2022.0  BONES AN
4          SMILE       2022.0      R   115.0        6.6        68          SMILE 2022.0  SMILE 20
5      BARBARIAN       2022.0      R   102.0        7.1        78      BARBARIAN 2022.0  BARBARIA

In [57]:
mergedf = pd.merge(imdbdf, wwbo, how='inner', on='match')

In [58]:
mergedf

Title_x Release Year_x     Rating Runtime IMDB Score     Metascore           Title and Year_x     match Release Year_y             Title_y   Worldwide      Domestic International         Title and Year_y
0              BARBARIAN         2022.0          R   102.0        7.1            78           BARBARIAN 2022.0  BARBARIA           2022           BARBARIAN  44,734,287  40,842,944.0   3,891,343.0           BARBARIAN 2022
1             BARBARIANS         2021.0  NO RATING    89.0        4.7            57          BARBARIANS 2021.0  BARBARIA           2022           BARBARIAN  44,734,287  40,842,944.0   3,891,343.0           BARBARIAN 2022
2            TERRIFIER 2         2022.0  Not Rated   138.0        6.3            59         TERRIFIER 2 2022.0  TERRIFIE           2022         TERRIFIER 2  11,287,125  10,640,105.0     647,020.0         TERRIFIER 2 2022
3              TERRIFIER         2016.0    Unrated    85.0        5.6  NO METASCORE           TERRIFIER 2016.0  TERRIFIE           2022         TERRIFIER 2  11,287,125  10,640,105.0     647,020.0         TERRIFIER 2 2022
4              TERRIFIED         2017.0  Not Rated    87.0        6.5  NO METASCORE           TERRIFIED 2017.0  TERRIFIE           2022         TERRIFIER 2  11,287,125  10,640,105.0     647,020.0         TERRIFIER 2 2022
...                  ...            ...        ...     ...        ...           ...                        ...       ...            ...                 ...         ...           ...           ...                      ...
5005           FRANCESCA         2015.0  NO RATING    80.0        5.3  NO METASCORE           FRANCESCA 2015.0  FRANCESC           2016           FRANCESCA       2,008           nan       2,008.0           FRANCESCA 2016
5006    KANCHANA: MUNI 2         2011.0  Not Rated   171.0        6.6  NO METASCORE    KANCHANA: MUNI 2 2011.0  KANCHANA           2019          KANCHANA 3      59,691           nan      59,691.0          KANCHANA 3 2019
5007           13 GRAVES         2019.0  NO RATING    83.0        4.6  NO METASCORE           13 GRAVES 2019.0  13 GRAVE           2019           13 GRAVES      10,921           nan      10,921.0           13 GRAVES 2019
5008         THE ANTENNA         2019.0  NO RATING   115.0        5.2            58         THE ANTENNA 2019.0  THE ANTE           2020         THE ANTENNA       2,983           nan       2,983.0         THE ANTENNA 2020
5009  ÜMMÜ SIBYAN: ZIFIR         2014.0  NO RATING     nan        2.7  NO METASCORE  ÜMMÜ SIBYAN: ZIFIR 2014.0  ÜMMÜ SIB           2014  ÜMMÜ SIBYAN: ZIFIR     526,724           nan     526,724.0  ÜMMÜ SIBYAN: ZIFIR 2014

[5010 rows x 14 columns]

In [59]:
mergedf['ratio'] = mergedf.apply((lambda x: fuzz.ratio(x['Title and Year_x'], x['Title and Year_y'])), axis=1)

In [60]:
mergedf.head()

Title_x Release Year_x     Rating Runtime IMDB Score     Metascore    Title and Year_x     match Release Year_y      Title_y   Worldwide      Domestic International  Title and Year_y  ratio
0    BARBARIAN         2022.0          R   102.0        7.1            78    BARBARIAN 2022.0  BARBARIA           2022    BARBARIAN  44,734,287  40,842,944.0   3,891,343.0    BARBARIAN 2022     93
1   BARBARIANS         2021.0  NO RATING    89.0        4.7            57   BARBARIANS 2021.0  BARBARIA           2022    BARBARIAN  44,734,287  40,842,944.0   3,891,343.0    BARBARIAN 2022     84
2  TERRIFIER 2         2022.0  Not Rated   138.0        6.3            59  TERRIFIER 2 2022.0  TERRIFIE           2022  TERRIFIER 2  11,287,125  10,640,105.0     647,020.0  TERRIFIER 2 2022     94
3    TERRIFIER         2016.0    Unrated    85.0        5.6  NO METASCORE    TERRIFIER 2016.0  TERRIFIE           2022  TERRIFIER 2  11,287,125  10,640,105.0     647,020.0  TERRIFIER 2 2022     75
4    TERRIFIED         2017.0  Not Rated    87.0        6.5  NO METASCORE    TERRIFIED 2017.0  TERRIFIE           2022  TERRIFIER 2  11,287,125  10,640,105.0     647,020.0  TERRIFIER 2 2022     69

In [61]:
mergedffilter = mergedf.loc[mergedf['ratio'] > 80]

In [62]:
mergedffilter
mergedffilter.index = np.arange(1, len(mergedffilter) + 1)

In [63]:
mergedffilter

Title_x Release Year_x     Rating Runtime IMDB Score     Metascore                    Title and Year_x     match Release Year_y                      Title_y    Worldwide       Domestic International                  Title and Year_y  ratio
1                       BARBARIAN         2022.0          R   102.0        7.1            78                    BARBARIAN 2022.0  BARBARIA           2022                    BARBARIAN   44,734,287   40,842,944.0   3,891,343.0                    BARBARIAN 2022     93
2                      BARBARIANS         2021.0  NO RATING    89.0        4.7            57                   BARBARIANS 2021.0  BARBARIA           2022                    BARBARIAN   44,734,287   40,842,944.0   3,891,343.0                    BARBARIAN 2022     84
3                     TERRIFIER 2         2022.0  Not Rated   138.0        6.3            59                  TERRIFIER 2 2022.0  TERRIFIE           2022                  TERRIFIER 2   11,287,125   10,640,105.0     647,020.0                  TERRIFIER 2 2022     94
4                        SCREAM 2         1997.0          R   120.0        6.3            63                     SCREAM 2 1997.0  SCREAM 2           1997                     SCREAM 2  172,363,301  101,363,301.0  71,000,000.0                     SCREAM 2 1997     93
5                     WHITE NOISE         2022.0          R   136.0        6.6            67                  WHITE NOISE 2022.0  WHITE NO           2005                  WHITE NOISE   92,094,360   56,094,360.0  36,000,000.0                  WHITE NOISE 2005     88
...                           ...            ...        ...     ...        ...           ...                                 ...       ...            ...                          ...          ...            ...           ...                               ...    ...
1224  SEYTANIN ÇOCUKLARI-EL EBYAZ         2016.0  NO RATING    92.0        3.6  NO METASCORE  SEYTANIN ÇOCUKLARI-EL EBYAZ 2016.0  SEYTANIN           2016  SEYTANIN ÇOCUKLARI-EL EBYAZ        3,893            nan       3,893.0  SEYTANIN ÇOCUKLARI-EL EBYAZ 2016     97
1225                    FRANCESCA         2015.0  NO RATING    80.0        5.3  NO METASCORE                    FRANCESCA 2015.0  FRANCESC           2016                    FRANCESCA        2,008            nan       2,008.0                    FRANCESCA 2016     87
1226                    13 GRAVES         2019.0  NO RATING    83.0        4.6  NO METASCORE                    13 GRAVES 2019.0  13 GRAVE           2019                    13 GRAVES       10,921            nan      10,921.0                    13 GRAVES 2019     93
1227                  THE ANTENNA         2019.0  NO RATING   115.0        5.2            58                  THE ANTENNA 2019.0  THE ANTE           2020                  THE ANTENNA        2,983            nan       2,983.0                  THE ANTENNA 2020     88
1228           ÜMMÜ SIBYAN: ZIFIR         2014.0  NO RATING     nan        2.7  NO METASCORE           ÜMMÜ SIBYAN: ZIFIR 2014.0  ÜMMÜ SIB           2014           ÜMMÜ SIBYAN: ZIFIR      526,724            nan     526,724.0           ÜMMÜ SIBYAN: ZIFIR 2014     96

[1228 rows x 15 columns]

In [64]:
mergedffilter = mergedffilter.drop(['Release Year_x', 'Title and Year_x', 'match', 'Title_y', 'Title and Year_y', 'ratio'], axis=1)

In [65]:
mergedffilter

Title_x     Rating Runtime IMDB Score     Metascore Release Year_y    Worldwide       Domestic International
1                       BARBARIAN          R   102.0        7.1            78           2022   44,734,287   40,842,944.0   3,891,343.0
2                      BARBARIANS  NO RATING    89.0        4.7            57           2022   44,734,287   40,842,944.0   3,891,343.0
3                     TERRIFIER 2  Not Rated   138.0        6.3            59           2022   11,287,125   10,640,105.0     647,020.0
4                        SCREAM 2          R   120.0        6.3            63           1997  172,363,301  101,363,301.0  71,000,000.0
5                     WHITE NOISE          R   136.0        6.6            67           2005   92,094,360   56,094,360.0  36,000,000.0
...                           ...        ...     ...        ...           ...            ...          ...            ...           ...
1224  SEYTANIN ÇOCUKLARI-EL EBYAZ  NO RATING    92.0        3.6  NO METASCORE           2016        3,893            nan       3,893.0
1225                    FRANCESCA  NO RATING    80.0        5.3  NO METASCORE           2016        2,008            nan       2,008.0
1226                    13 GRAVES  NO RATING    83.0        4.6  NO METASCORE           2019       10,921            nan      10,921.0
1227                  THE ANTENNA  NO RATING   115.0        5.2            58           2020        2,983            nan       2,983.0
1228           ÜMMÜ SIBYAN: ZIFIR  NO RATING     nan        2.7  NO METASCORE           2014      526,724            nan     526,724.0

[1228 rows x 9 columns]

In [66]:
cleanmerge = mergedffilter.rename(columns={'Title_x': 'Title', 'Release Year_y': 'Release Year'})

In [67]:
pd.set_option('display.max_rows', None)

In [68]:
cleanmerge

Title     Rating Runtime      IMDB Score     Metascore Release Year    Worldwide       Domestic  International
1                                            BARBARIAN          R   102.0             7.1            78         2022   44,734,287   40,842,944.0    3,891,343.0
2                                           BARBARIANS  NO RATING    89.0             4.7            57         2022   44,734,287   40,842,944.0    3,891,343.0
3                                          TERRIFIER 2  Not Rated   138.0             6.3            59         2022   11,287,125   10,640,105.0      647,020.0
4                                             SCREAM 2          R   120.0             6.3            63         1997  172,363,301  101,363,301.0   71,000,000.0
5                                          WHITE NOISE          R   136.0             6.6            67         2005   92,094,360   56,094,360.0   36,000,000.0
6                                          WHITE NOISE      PG-13   101.0             5.5            30         2005   92,094,360   56,094,360.0   36,000,000.0
7                             WHITE NOISE 2: THE LIGHT      PG-13    99.0             5.7  NO METASCORE         2008    8,243,567            nan    8,243,567.0
8                                SOMETHING IN THE DIRT          R   116.0             6.0            76         2022      107,114            nan      107,114.0
9                               SOMETHING IN THE WOODS  NO RATING    76.0             2.6  NO METASCORE         2022      107,114            nan      107,114.0
10                                           MIDSOMMAR          R   148.0             7.1            72         2019   46,757,893   27,426,363.0   19,331,530.0
11                                    AMERICAN CARNAGE          R   101.0             4.8  NO METASCORE         2022       46,389            nan       46,389.0
12                                BODIES BODIES BODIES          R    94.0             6.3            69         2022   13,454,835   11,446,602.0    2,008,233.0
13                                        DOCTOR SLEEP          R   152.0             7.3            59         2019   71,720,838   31,581,712.0   40,139,126.0
14                                     THE BLACK PHONE          R   103.0             6.9            65         2022  161,204,799   89,887,230.0   71,317,569.0
15                            THE BLACKCOAT'S DAUGHTER          R    93.0             5.9            68         2017      143,545       20,435.0      123,110.0
16                                CRIMES OF THE FUTURE          R   107.0             5.9            67         2022    3,600,102    2,452,882.0    1,147,220.0
17                                      THE INVITATION      PG-13   105.0             5.2            45         2022   33,689,288   25,100,080.0    8,589,208.0
18                                   THE INVISIBLE MAN          R   124.0             7.1            72         2020  139,011,965   64,914,050.0   74,097,915.0
19                                      THE INVITATION  Not Rated   100.0             6.6            74         2022   33,689,288   25,100,080.0    8,589,208.0
20                                   THE INVISIBLE MAN      TV-PG    71.0             7.6            87         2020  139,011,965   64,914,050.0   74,097,915.0
21                                   THE INVISIBLE MAN      TV-PG    71.0             7.6            87         1933          132            nan          132.0
22                                THE INVISIBLE MANIAC          R    86.0             4.1  NO METASCORE         2020  139,011,965   64,914,050.0   74,097,915.0
23                                THE INVISIBLE MANIAC          R    86.0             4.1  NO METASCORE         1933          132            nan          132.0
24                                   THE INVISIBLE RAY   Approved    80.0             6.5  NO METASCORE         1933          132            nan          132.0
25                                         THE SH

In [69]:
duplicateRows = cleanmerge[cleanmerge.duplicated(['Title'])]

In [70]:
duplicateRows

Title     Rating Runtime      IMDB Score     Metascore Release Year    Worldwide       Domestic  International
6                                       WHITE NOISE      PG-13   101.0             5.5            30         2005   92,094,360   56,094,360.0   36,000,000.0
19                                   THE INVITATION  Not Rated   100.0             6.6            74         2022   33,689,288   25,100,080.0    8,589,208.0
20                                THE INVISIBLE MAN      TV-PG    71.0             7.6            87         2020  139,011,965   64,914,050.0   74,097,915.0
21                                THE INVISIBLE MAN      TV-PG    71.0             7.6            87         1933          132            nan          132.0
23                             THE INVISIBLE MANIAC          R    86.0             4.1  NO METASCORE         1933          132            nan          132.0
27                                       HELLRAISER          R    94.0             6.9            56         1987   14,575,148   14,564,000.0       11,148.0
33                                        HALLOWEEN          R   106.0             6.5            67         2018  255,416,089  159,366,015.0   96,050,074.0
34                                        HALLOWEEN          R   106.0             6.5            67         2007   77,514,401   58,269,151.0   19,245,250.0
35                                        HALLOWEEN          R   106.0             6.5            67         2009   38,512,850   33,392,973.0    5,119,877.0
36                                        HALLOWEEN          R   109.0             6.0            47         2007   77,514,401   58,269,151.0   19,245,250.0
37                                        HALLOWEEN          R   109.0             6.0            47         2009   38,512,850   33,392,973.0    5,119,877.0
39                                     HALLOWEEN II          R   105.0             4.8            35         2009   38,512,850   33,392,973.0    5,119,877.0
42         HALLOWEEN 4: THE RETURN OF MICHAEL MYERS          R    88.0             5.8            34         1995   15,126,948   15,126,948.0            nan
43         HALLOWEEN 4: THE RETURN OF MICHAEL MYERS          R    88.0             5.8            34         1989   11,642,254   11,642,254.0            nan
45            HALLOWEEN: THE CURSE OF MICHAEL MYERS          R    87.0             4.7            10         1995   15,126,948   15,126,948.0            nan
46            HALLOWEEN: THE CURSE OF MICHAEL MYERS          R    87.0             4.7            10         1989   11,642,254   11,642,254.0            nan
49        HALLOWEEN 5: THE REVENGE OF MICHAEL MYERS          R    96.0             4.9            28         1995   15,126,948   15,126,948.0            nan
50        HALLOWEEN 5: THE REVENGE OF MICHAEL MYERS          R    96.0             4.9            28         1989   11,642,254   11,642,254.0            nan
53                                         SUSPIRIA          R    92.0             7.3            79         1977       35,694            nan       35,694.0
56                                    SPEAK NO EVIL          R    74.0             3.4  NO METASCORE         2014      247,345            nan      247,345.0
65                                 JEEPERS CREEPERS          R    90.0             6.2            49         2003  119,923,801   35,623,801.0   84,300,000.0
66                                 JEEPERS CREEPERS          R    90.0             6.2            49         2017    3,634,435    2,235,162.0    1,399,273.0
68                               JEEPERS CREEPERS 2          R   104.0             5.6            36         2003  119,923,801   35,623,801.0   84,300,000.0
69                               JEEPERS CREEPERS 2          R   104.0             5.6            36         2017    3,634,435    2,235,162.0    1,399,273.0
71                             JEEPERS CREEPERS III  Not Rated   100.0             3.9  NO METASCORE         2003  119,92

In [71]:
len(duplicateRows)

252

In [72]:
cleanmerge = cleanmerge[cleanmerge['Metascore'] != 'NO METASCORE']

In [73]:
cleanmerge

Title     Rating Runtime IMDB Score Metascore Release Year    Worldwide       Domestic  International
1                                            BARBARIAN          R   102.0        7.1        78         2022   44,734,287   40,842,944.0    3,891,343.0
2                                           BARBARIANS  NO RATING    89.0        4.7        57         2022   44,734,287   40,842,944.0    3,891,343.0
3                                          TERRIFIER 2  Not Rated   138.0        6.3        59         2022   11,287,125   10,640,105.0      647,020.0
4                                             SCREAM 2          R   120.0        6.3        63         1997  172,363,301  101,363,301.0   71,000,000.0
5                                          WHITE NOISE          R   136.0        6.6        67         2005   92,094,360   56,094,360.0   36,000,000.0
6                                          WHITE NOISE      PG-13   101.0        5.5        30         2005   92,094,360   56,094,360.0   36,000,000.0
8                                SOMETHING IN THE DIRT          R   116.0        6.0        76         2022      107,114            nan      107,114.0
10                                           MIDSOMMAR          R   148.0        7.1        72         2019   46,757,893   27,426,363.0   19,331,530.0
12                                BODIES BODIES BODIES          R    94.0        6.3        69         2022   13,454,835   11,446,602.0    2,008,233.0
13                                        DOCTOR SLEEP          R   152.0        7.3        59         2019   71,720,838   31,581,712.0   40,139,126.0
14                                     THE BLACK PHONE          R   103.0        6.9        65         2022  161,204,799   89,887,230.0   71,317,569.0
15                            THE BLACKCOAT'S DAUGHTER          R    93.0        5.9        68         2017      143,545       20,435.0      123,110.0
16                                CRIMES OF THE FUTURE          R   107.0        5.9        67         2022    3,600,102    2,452,882.0    1,147,220.0
17                                      THE INVITATION      PG-13   105.0        5.2        45         2022   33,689,288   25,100,080.0    8,589,208.0
18                                   THE INVISIBLE MAN          R   124.0        7.1        72         2020  139,011,965   64,914,050.0   74,097,915.0
19                                      THE INVITATION  Not Rated   100.0        6.6        74         2022   33,689,288   25,100,080.0    8,589,208.0
20                                   THE INVISIBLE MAN      TV-PG    71.0        7.6        87         2020  139,011,965   64,914,050.0   74,097,915.0
21                                   THE INVISIBLE MAN      TV-PG    71.0        7.6        87         1933          132            nan          132.0
25                                         THE SHINING          R   146.0        8.4        66         1980   45,601,938   44,568,631.0    1,033,307.0
26                                          HELLRAISER          R   121.0        6.0        55         2021       12,640            nan       12,640.0
27                                          HELLRAISER          R    94.0        6.9        56         1987   14,575,148   14,564,000.0       11,148.0
28                       HELLRAISER III: HELL ON EARTH          R    97.0        5.5        50         1992   12,525,537   12,525,537.0            nan
29                               HELLRAISER: BLOODLINE          R    85.0        5.0        21         1996    9,321,492    9,321,492.0            nan
30                                      HALLOWEEN ENDS          R   111.0        5.0        47         2022  105,010,237   64,079,860.0   40,930,377.0
31                                           HALLOWEEN          R    91.0        7.7        87         1978   70,274,000   47,274,000.0   23,000,000.0
32                                     HALLOWEEN KILLS          R   105.0        5.5        42         2021  130,851,162   

In [74]:
cleanmerge.to_csv('cleanmerge.csv')

MOVIES RANKED BY IMDB SCORE

In [135]:
rankbyimdb = cleanmerge.sort_values(by=['IMDB Score'], ascending=False)
rankbyimdb.index = np.arange(1, len(rankbyimdb) + 1)

In [137]:
rankbyimdb.head(15)

Title     Rating  Runtime IMDB Score  Metascore  Release Year  Worldwide     Domestic  International
1                      THE SHINING          R    146.0        8.4         66          1980   45601938   44568631.0            NaN
2                        THE THING          R    109.0        8.2         57          1982   13841714   13782838.0            NaN
3                     THE EXORCIST          R    122.0        8.1         81          1973  428214478  230347346.0            NaN
4                  ROSEMARY'S BABY   Approved    137.0        8.0         96          1968   33396740   33395426.0            NaN
5                        KING KONG     Passed    100.0        7.9         90          1933   10001781   10000000.0            NaN
6                 DAWN OF THE DEAD    Unrated    127.0        7.8         71          2004  103452875   58990765.0            NaN
7                 DAWN OF THE DEAD    Unrated    127.0        7.8         71          1979   55000000    5100000.0            NaN
8                     FRANKENSTEIN     Passed     70.0        7.8         91          1931   12001435   12000000.0            NaN
9                     FRANKENSTEIN     Passed     70.0        7.8         91          1994  112006296   22006296.0            NaN
10        NIGHT OF THE LIVING DEAD  Not Rated     96.0        7.8         89          1968   30087064   12087064.0            NaN
11        NIGHT OF THE LIVING DEAD  Not Rated     96.0        7.8         89          1990    5835247    5835247.0            NaN
12  INVASION OF THE BODY SNATCHERS   Approved     80.0        7.7         92          1956       2044          NaN            NaN
13                    EVIL DEAD II          R     84.0        7.7         72          1987    5927557    5923044.0            NaN
14  INVASION OF THE BODY SNATCHERS   Approved     80.0        7.7         92          1978   24946533   24946533.0            NaN
15                       HALLOWEEN          R     91.0        7.7         87          1978   70274000   47274000.0            NaN

In [138]:
rankbyimdb = rankbyimdb.drop(6)
rankbyimdb = rankbyimdb.drop(9)
rankbyimdb = rankbyimdb.drop(11)

In [153]:
rankbyimdb.index = np.arange(1, len(rankbyimdb) + 1)
rankbyimdb.head(10)

Title     Rating  Runtime IMDB Score  Metascore  Release Year  Worldwide     Domestic  International
1                      THE SHINING          R    146.0        8.4         66          1980   45601938   44568631.0            NaN
2                        THE THING          R    109.0        8.2         57          1982   13841714   13782838.0            NaN
3                     THE EXORCIST          R    122.0        8.1         81          1973  428214478  230347346.0            NaN
4                  ROSEMARY'S BABY   Approved    137.0        8.0         96          1968   33396740   33395426.0            NaN
5                        KING KONG     Passed    100.0        7.9         90          1933   10001781   10000000.0            NaN
6                 DAWN OF THE DEAD    Unrated    127.0        7.8         71          1979   55000000    5100000.0            NaN
7                     FRANKENSTEIN     Passed     70.0        7.8         91          1931   12001435   12000000.0            NaN
8         NIGHT OF THE LIVING DEAD  Not Rated     96.0        7.8         89          1968   30087064   12087064.0            NaN
9   INVASION OF THE BODY SNATCHERS   Approved     80.0        7.7         92          1956       2044          NaN            NaN
10                    EVIL DEAD II          R     84.0        7.7         72          1987    5927557    5923044.0            NaN

In [160]:
rankbyimdb = rankbyimdb.drop('Rating', axis=1)
rankbyimdb = rankbyimdb.drop('Runtime', axis=1)

KeyError: "['Rating'] not found in axis"

In [162]:
rankbyimdb = rankbyimdb.drop('Metascore', axis=1)

In [163]:
rankbyimdb

Title IMDB Score  Release Year  Worldwide     Domestic  International
1                                         THE SHINING        8.4          1980   45601938   44568631.0            NaN
2                                           THE THING        8.2          1982   13841714   13782838.0            NaN
3                                        THE EXORCIST        8.1          1973  428214478  230347346.0            NaN
4                                     ROSEMARY'S BABY        8.0          1968   33396740   33395426.0            NaN
5                                           KING KONG        7.9          1933   10001781   10000000.0            NaN
6                                    DAWN OF THE DEAD        7.8          1979   55000000    5100000.0            NaN
7                                        FRANKENSTEIN        7.8          1931   12001435   12000000.0            NaN
8                            NIGHT OF THE LIVING DEAD        7.8          1968   30087064   12087064.0            NaN
9                      INVASION OF THE BODY SNATCHERS        7.7          1956       2044          NaN            NaN
10                                       EVIL DEAD II        7.7          1987    5927557    5923044.0            NaN
11                     INVASION OF THE BODY SNATCHERS        7.7          1978   24946533   24946533.0            NaN
12                                          HALLOWEEN        7.7          1978   70274000   47274000.0            NaN
13                                  THE INVISIBLE MAN        7.6          1933        132          NaN          132.0
14                                          THE BIRDS        7.6          1963   11436929   11403529.0            NaN
15                                         THE OTHERS        7.6          2001  207765056   96522687.0            NaN
16                                  THE INVISIBLE MAN        7.6          2020  139011965   64914050.0            NaN
17                                     THE WICKER MAN        7.5          1973     177554      58341.0            NaN
18                                      A QUIET PLACE        7.5          2018  334876670  188024361.0            NaN
19                                      THE CONJURING        7.5          2013  317740900  137400141.0            NaN
20                                   28 DAYS LATER...        7.5          2003   82955633   45064915.0            NaN
21                     AN AMERICAN WEREWOLF IN LONDON        7.5          1981   61968388   31973249.0            NaN
22                                           THE OMEN        7.5          1976   48577431   48570885.0            NaN
23                       THE TEXAS CHAIN SAW MASSACRE        7.4          1986    8025872    8025872.0            NaN
24                     INVASION OF THE BODY SNATCHERS        7.4          1956       2044          NaN            NaN
25                                       THE HAUNTING        7.4          1999  180188905   91188905.0            NaN
26                     INVASION OF THE BODY SNATCHERS        7.4          1978   24946533   24946533.0            NaN
27                          A NIGHTMARE ON ELM STREET        7.4          1984   25542906   25504513.0            NaN
28                          A NIGHTMARE ON ELM STREET        7.4          2010  117729618   63075011.0            NaN
29                               THE DEVIL'S BACKBONE        7.4          2001     755249     755249.0            NaN
30                                      THE EVIL DEAD        7.4          1983   29400000    2400000.0            NaN
31                       THE TEXAS CHAIN SAW MASSACRE        7.4          2003  107967319   80571655.0            NaN
32                                   ARMY OF DARKNESS        7.4          1993   21502976   11502976.0            NaN
33                       THE TEXAS CHAIN SAW MASSACRE        7.4          1974   26572439   26572439.0            NaN
34                                  

In [147]:
cleanmerge['Metascore'] = pd.to_numeric(cleanmerge['Metascore'], errors='coerce')

C:\Users\rober\AppData\Local\Temp\ipykernel_23112\920940606.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Metascore'] = pd.to_numeric(cleanmerge['Metascore'], errors='coerce')


MOVIES RANKED BY METASCORE

In [148]:
rankmeta = cleanmerge.sort_values(by=['Metascore'], ascending=False)
rankmeta.index = np.arange(1, len(rankmeta) + 1)
rankmeta = rankmeta[rankmeta['Metascore'] != 'nan']
rankmeta = rankmeta.drop('IMDB Score', axis=1)

In [149]:
rankmeta

Title     Rating  Runtime  Metascore  Release Year  Worldwide     Domestic  International
1                                     ROSEMARY'S BABY   Approved    137.0         96          1968   33396740   33395426.0            NaN
2                      INVASION OF THE BODY SNATCHERS   Approved     80.0         92          1978   24946533   24946533.0            NaN
3                      INVASION OF THE BODY SNATCHERS   Approved     80.0         92          1956       2044          NaN            NaN
4                                        FRANKENSTEIN     Passed     70.0         91          1994  112006296   22006296.0            NaN
5                                        FRANKENSTEIN     Passed     70.0         91          1931   12001435   12000000.0            NaN
6                                           KING KONG     Passed    100.0         90          1933   10001781   10000000.0            NaN
7                                           THE BIRDS      PG-13    119.0         90          1963   11436929   11403529.0            NaN
8                            NIGHT OF THE LIVING DEAD  Not Rated     96.0         89          1968   30087064   12087064.0            NaN
9                            NIGHT OF THE LIVING DEAD  Not Rated     96.0         89          1990    5835247    5835247.0            NaN
10                                          HALLOWEEN          R     91.0         87          1978   70274000   47274000.0            NaN
11                                     THE WICKER MAN          R     88.0         87          1973     177554      58341.0            NaN
12                                         ERASERHEAD  Not Rated     89.0         87          1977    7097971    7000000.0            NaN
13                                         HEREDITARY          R    127.0         87          2018   81263489   44069456.0            NaN
14                                  THE INVISIBLE MAN      TV-PG     71.0         87          2020  139011965   64914050.0            NaN
15                                  THE INVISIBLE MAN      TV-PG     71.0         87          1933        132          NaN          132.0
16                                       THE BABADOOK  Not Rated     94.0         86          2014    7482387     950792.0            NaN
17                                         IT FOLLOWS          R    100.0         83          2015   23236296   14674077.0            NaN
18                                   UNDER THE SHADOW      PG-13     84.0         83          2016     151923      28884.0            NaN
19                                     THE LIGHTHOUSE          R    109.0         83          2019   18262307   10867104.0            NaN
20                                    DRAG ME TO HELL      PG-13     99.0         83          2009   91388487   42100625.0            NaN
21                                      A QUIET PLACE      PG-13     90.0         82          2018  334876670  188024361.0            NaN
22                                       THE EXORCIST          R    122.0         81          1973  428214478  230347346.0            NaN
23                            THE BLAIR WITCH PROJECT          R     81.0         81          1999  248300000  140539099.0            NaN
24                   A GIRL WALKS HOME ALONE AT NIGHT  Not Rated    101.0         81          2014     628020     544032.0            NaN
25                       THE TEXAS CHAIN SAW MASSACRE          R     83.0         80          1986    8025872    8025872.0            NaN
26                       THE TEXAS CHAIN SAW MASSACRE          R     83.0         80          2003  107967319   80571655.0            NaN
27                             BERBERIAN SOUND STUDIO  Not Rated     92.0         80          2012     279142      31641.0            NaN
28                       THE TEXAS CHAIN SAW MASSACRE          R     83.0         80          1974   26572439   26572439.0            NaN
29                                          LE

In [150]:
rankmeta = rankmeta.drop(2)
rankmeta = rankmeta.drop(4)
rankmeta = rankmeta.drop(9)
rankmeta = rankmeta.drop(2)

KeyError: '[2] not found in axis'

In [152]:
rankmeta.index = np.arange(1, len(rankmeta) + 1)
rankmeta

Title     Rating  Runtime  Metascore  Release Year  Worldwide     Domestic  International
1                                     ROSEMARY'S BABY   Approved    137.0         96          1968   33396740   33395426.0            NaN
2                      INVASION OF THE BODY SNATCHERS   Approved     80.0         92          1956       2044          NaN            NaN
3                                        FRANKENSTEIN     Passed     70.0         91          1931   12001435   12000000.0            NaN
4                                           KING KONG     Passed    100.0         90          1933   10001781   10000000.0            NaN
5                                           THE BIRDS      PG-13    119.0         90          1963   11436929   11403529.0            NaN
6                            NIGHT OF THE LIVING DEAD  Not Rated     96.0         89          1968   30087064   12087064.0            NaN
7                                           HALLOWEEN          R     91.0         87          1978   70274000   47274000.0            NaN
8                                      THE WICKER MAN          R     88.0         87          1973     177554      58341.0            NaN
9                                          ERASERHEAD  Not Rated     89.0         87          1977    7097971    7000000.0            NaN
10                                         HEREDITARY          R    127.0         87          2018   81263489   44069456.0            NaN
11                                  THE INVISIBLE MAN      TV-PG     71.0         87          2020  139011965   64914050.0            NaN
12                                  THE INVISIBLE MAN      TV-PG     71.0         87          1933        132          NaN          132.0
13                                       THE BABADOOK  Not Rated     94.0         86          2014    7482387     950792.0            NaN
14                                         IT FOLLOWS          R    100.0         83          2015   23236296   14674077.0            NaN
15                                   UNDER THE SHADOW      PG-13     84.0         83          2016     151923      28884.0            NaN
16                                     THE LIGHTHOUSE          R    109.0         83          2019   18262307   10867104.0            NaN
17                                    DRAG ME TO HELL      PG-13     99.0         83          2009   91388487   42100625.0            NaN
18                                      A QUIET PLACE      PG-13     90.0         82          2018  334876670  188024361.0            NaN
19                                       THE EXORCIST          R    122.0         81          1973  428214478  230347346.0            NaN
20                            THE BLAIR WITCH PROJECT          R     81.0         81          1999  248300000  140539099.0            NaN
21                   A GIRL WALKS HOME ALONE AT NIGHT  Not Rated    101.0         81          2014     628020     544032.0            NaN
22                       THE TEXAS CHAIN SAW MASSACRE          R     83.0         80          1986    8025872    8025872.0            NaN
23                       THE TEXAS CHAIN SAW MASSACRE          R     83.0         80          2003  107967319   80571655.0            NaN
24                             BERBERIAN SOUND STUDIO  Not Rated     92.0         80          2012     279142      31641.0            NaN
25                       THE TEXAS CHAIN SAW MASSACRE          R     83.0         80          1974   26572439   26572439.0            NaN
26                                          LET ME IN          R    116.0         79          2010   28270399   12134935.0            NaN
27                                        POLTERGEIST         PG    114.0         79          1982  121706019   74706019.0            NaN
28                                           SUSPIRIA          R     92.0         79          1977      35694          NaN            NaN
29                                         LA 

In [166]:
rankmeta = rankmeta.drop('Rating', axis=1)
rankmeta = rankmeta.drop('Runtime', axis=1)

In [171]:
rankmeta

Title  Metascore  Release Year  Worldwide     Domestic  International
1                                     ROSEMARY'S BABY         96          1968   33396740   33395426.0            NaN
2                      INVASION OF THE BODY SNATCHERS         92          1956       2044          NaN            NaN
3                                        FRANKENSTEIN         91          1931   12001435   12000000.0            NaN
4                                           KING KONG         90          1933   10001781   10000000.0            NaN
5                                           THE BIRDS         90          1963   11436929   11403529.0            NaN
6                            NIGHT OF THE LIVING DEAD         89          1968   30087064   12087064.0            NaN
7                                           HALLOWEEN         87          1978   70274000   47274000.0            NaN
8                                      THE WICKER MAN         87          1973     177554      58341.0            NaN
9                                          ERASERHEAD         87          1977    7097971    7000000.0            NaN
10                                         HEREDITARY         87          2018   81263489   44069456.0            NaN
11                                  THE INVISIBLE MAN         87          2020  139011965   64914050.0            NaN
12                                  THE INVISIBLE MAN         87          1933        132          NaN          132.0
13                                       THE BABADOOK         86          2014    7482387     950792.0            NaN
14                                         IT FOLLOWS         83          2015   23236296   14674077.0            NaN
15                                   UNDER THE SHADOW         83          2016     151923      28884.0            NaN
16                                     THE LIGHTHOUSE         83          2019   18262307   10867104.0            NaN
17                                    DRAG ME TO HELL         83          2009   91388487   42100625.0            NaN
18                                      A QUIET PLACE         82          2018  334876670  188024361.0            NaN
19                                       THE EXORCIST         81          1973  428214478  230347346.0            NaN
20                            THE BLAIR WITCH PROJECT         81          1999  248300000  140539099.0            NaN
21                   A GIRL WALKS HOME ALONE AT NIGHT         81          2014     628020     544032.0            NaN
22                       THE TEXAS CHAIN SAW MASSACRE         80          1986    8025872    8025872.0            NaN
23                       THE TEXAS CHAIN SAW MASSACRE         80          2003  107967319   80571655.0            NaN
24                             BERBERIAN SOUND STUDIO         80          2012     279142      31641.0            NaN
25                       THE TEXAS CHAIN SAW MASSACRE         80          1974   26572439   26572439.0            NaN
26                                          LET ME IN         79          2010   28270399   12134935.0            NaN
27                                        POLTERGEIST         79          1982  121706019   74706019.0            NaN
28                                           SUSPIRIA         79          1977      35694          NaN            NaN
29                                         LA LLORONA         79          2020     300173          NaN            NaN
30                                         GREEN ROOM         79          2016    3807503    3220371.0            NaN
31                                       FLUX GOURMET         79          2022      80101      19222.0            NaN
32                                      SPEAK NO EVIL         78          2014     247345          NaN            NaN
33                                  IT COMES AT NIGHT         78          2017   19720203   13985117.0            NaN
34                                  

In [172]:
rankmetabtm = cleanmerge.sort_values(by=['Metascore'], ascending=True)
rankmetabtm.index = np.arange(1, len(rankmetabtm) + 1)

In [173]:
rankmetabtm

Title     Rating  Runtime IMDB Score  Metascore  Release Year  Worldwide     Domestic  International
1            THE HUMAN CENTIPEDE III (FINAL SEQUENCE)  Not Rated    102.0        2.8          5          2015      18976      14562.0            NaN
2                                         THE MANGLER          R    106.0        4.3          8          1995    1781000    1781000.0            NaN
3                                   ALONE IN THE DARK          R     96.0        2.4          9          2005   10588079    5178569.0            NaN
4               HALLOWEEN: THE CURSE OF MICHAEL MYERS          R     87.0        4.7         10          1988   17768757   17768757.0            NaN
5               HALLOWEEN: THE CURSE OF MICHAEL MYERS          R     87.0        4.7         10          1989   11642254   11642254.0            NaN
6               HALLOWEEN: THE CURSE OF MICHAEL MYERS          R     87.0        4.7         10          1995   15126948   15126948.0            NaN
7                                NOTHING LEFT TO FEAR          R    100.0        4.4         12          2013    1675381       7886.0            NaN
8             FRIDAY THE 13TH PART VII: THE NEW BLOOD          R     88.0        5.2         13          1988   19170001   19170001.0            NaN
9    FRIDAY THE 13TH PART VIII: JASON TAKES MANHATTAN          R    100.0        4.5         14          1989   14343976   14343976.0            NaN
10                                        CABIN FEVER          R     99.0        3.7         14          2003   30351664   21158188.0            NaN
11                     BOOK OF SHADOWS: BLAIR WITCH 2          R     90.0        4.0         15          2000   47721314   26421314.0            NaN
12                                  HOUSE OF THE DEAD          R     90.0        2.1         15          2003   13860078   10199354.0            NaN
13                                           DARKNESS      PG-13     88.0        5.4         15          2004   34409206   22163442.0            NaN
14                                         FEARDOTCOM          R    101.0        3.4         16          2002   13289290   13208023.0            NaN
15                            SILENT HILL: REVELATION          R     95.0        4.9         16          2012   55975672   17530219.0            NaN
16                           URBAN LEGENDS: FINAL CUT          R     97.0        4.3         16          2000   38574362   21468807.0            NaN
17                                         LOST SOULS          R     97.0        4.8         16          2000   31320293   16779636.0            NaN
18                   FRIDAY THE 13TH: A NEW BEGINNING          R     92.0        4.7         16          1985   21930418   21930418.0            NaN
19               JASON GOES TO HELL: THE FINAL FRIDAY          R     87.0        4.1         17          1993   15935068   15935068.0            NaN
20                                         LEPRECHAUN          R     92.0        4.8         17          1994    2217237    2217237.0            NaN
21                                        SEE NO EVIL          R     84.0        5.0         17          2006   18828036   15032800.0            NaN
22                                         LEPRECHAUN          R     92.0        4.8         17          1993    8533294    8533294.0            NaN
23                                    BLESS THE CHILD          R    107.0        5.1         17          2000   40435694   29374178.0            NaN
24              THE HUMAN CENTIPEDE 2 (FULL SEQUENCE)  Not Rated     91.0        3.8         17          2015      18976      14562.0            NaN
25                                         PROM NIGHT      PG-13     88.0        3.9         17          2008   57193655   43869350.0            NaN
26                                          VALENTINE          R     96.0        4.8         18          2001   20384136   20384136.0            NaN
27                       

In [174]:
rankmetabtm = rankmetabtm.drop(4)
rankmetabtm = rankmetabtm.drop(5)
rankmetabtm = rankmetabtm.drop(10)

In [175]:
rankmetabtm

Title     Rating  Runtime IMDB Score  Metascore  Release Year  Worldwide     Domestic  International
1            THE HUMAN CENTIPEDE III (FINAL SEQUENCE)  Not Rated    102.0        2.8          5          2015      18976      14562.0            NaN
2                                         THE MANGLER          R    106.0        4.3          8          1995    1781000    1781000.0            NaN
3                                   ALONE IN THE DARK          R     96.0        2.4          9          2005   10588079    5178569.0            NaN
6               HALLOWEEN: THE CURSE OF MICHAEL MYERS          R     87.0        4.7         10          1995   15126948   15126948.0            NaN
7                                NOTHING LEFT TO FEAR          R    100.0        4.4         12          2013    1675381       7886.0            NaN
8             FRIDAY THE 13TH PART VII: THE NEW BLOOD          R     88.0        5.2         13          1988   19170001   19170001.0            NaN
9    FRIDAY THE 13TH PART VIII: JASON TAKES MANHATTAN          R    100.0        4.5         14          1989   14343976   14343976.0            NaN
11                     BOOK OF SHADOWS: BLAIR WITCH 2          R     90.0        4.0         15          2000   47721314   26421314.0            NaN
12                                  HOUSE OF THE DEAD          R     90.0        2.1         15          2003   13860078   10199354.0            NaN
13                                           DARKNESS      PG-13     88.0        5.4         15          2004   34409206   22163442.0            NaN
14                                         FEARDOTCOM          R    101.0        3.4         16          2002   13289290   13208023.0            NaN
15                            SILENT HILL: REVELATION          R     95.0        4.9         16          2012   55975672   17530219.0            NaN
16                           URBAN LEGENDS: FINAL CUT          R     97.0        4.3         16          2000   38574362   21468807.0            NaN
17                                         LOST SOULS          R     97.0        4.8         16          2000   31320293   16779636.0            NaN
18                   FRIDAY THE 13TH: A NEW BEGINNING          R     92.0        4.7         16          1985   21930418   21930418.0            NaN
19               JASON GOES TO HELL: THE FINAL FRIDAY          R     87.0        4.1         17          1993   15935068   15935068.0            NaN
20                                         LEPRECHAUN          R     92.0        4.8         17          1994    2217237    2217237.0            NaN
21                                        SEE NO EVIL          R     84.0        5.0         17          2006   18828036   15032800.0            NaN
22                                         LEPRECHAUN          R     92.0        4.8         17          1993    8533294    8533294.0            NaN
23                                    BLESS THE CHILD          R    107.0        5.1         17          2000   40435694   29374178.0            NaN
24              THE HUMAN CENTIPEDE 2 (FULL SEQUENCE)  Not Rated     91.0        3.8         17          2015      18976      14562.0            NaN
25                                         PROM NIGHT      PG-13     88.0        3.9         17          2008   57193655   43869350.0            NaN
26                                          VALENTINE          R     96.0        4.8         18          2001   20384136   20384136.0            NaN
27                                   THE DARKEST HOUR      PG-13     89.0        4.9         18          2005        423        423.0            NaN
28                                   THE DEVIL INSIDE          R     83.0        4.2         18          2012  101759490   53262945.0            NaN
29                                     THE APPARITION      PG-13     82.0        4.1         18          2012   10637281    4936819.0            NaN
30       CHILDREN OF THE 

In [179]:
rankmetabtm.index = np.arange(1, len(rankmetabtm) + 1)

In [181]:
rankmetabtm = rankmetabtm.drop('Rating', axis=1)
rankmetabtm = rankmetabtm.drop('Runtime', axis=1)
rankmetabtm = rankmetabtm.drop('IMDB Score', axis=1)
rankmetabtm

Title  Metascore  Release Year  Worldwide     Domestic  International
1            THE HUMAN CENTIPEDE III (FINAL SEQUENCE)          5          2015      18976      14562.0            NaN
2                                         THE MANGLER          8          1995    1781000    1781000.0            NaN
3                                   ALONE IN THE DARK          9          2005   10588079    5178569.0            NaN
4               HALLOWEEN: THE CURSE OF MICHAEL MYERS         10          1995   15126948   15126948.0            NaN
5                                NOTHING LEFT TO FEAR         12          2013    1675381       7886.0            NaN
6             FRIDAY THE 13TH PART VII: THE NEW BLOOD         13          1988   19170001   19170001.0            NaN
7    FRIDAY THE 13TH PART VIII: JASON TAKES MANHATTAN         14          1989   14343976   14343976.0            NaN
8                      BOOK OF SHADOWS: BLAIR WITCH 2         15          2000   47721314   26421314.0            NaN
9                                   HOUSE OF THE DEAD         15          2003   13860078   10199354.0            NaN
10                                           DARKNESS         15          2004   34409206   22163442.0            NaN
11                                         FEARDOTCOM         16          2002   13289290   13208023.0            NaN
12                            SILENT HILL: REVELATION         16          2012   55975672   17530219.0            NaN
13                           URBAN LEGENDS: FINAL CUT         16          2000   38574362   21468807.0            NaN
14                                         LOST SOULS         16          2000   31320293   16779636.0            NaN
15                   FRIDAY THE 13TH: A NEW BEGINNING         16          1985   21930418   21930418.0            NaN
16               JASON GOES TO HELL: THE FINAL FRIDAY         17          1993   15935068   15935068.0            NaN
17                                         LEPRECHAUN         17          1994    2217237    2217237.0            NaN
18                                        SEE NO EVIL         17          2006   18828036   15032800.0            NaN
19                                         LEPRECHAUN         17          1993    8533294    8533294.0            NaN
20                                    BLESS THE CHILD         17          2000   40435694   29374178.0            NaN
21              THE HUMAN CENTIPEDE 2 (FULL SEQUENCE)         17          2015      18976      14562.0            NaN
22                                         PROM NIGHT         17          2008   57193655   43869350.0            NaN
23                                          VALENTINE         18          2001   20384136   20384136.0            NaN
24                                   THE DARKEST HOUR         18          2005        423        423.0            NaN
25                                   THE DEVIL INSIDE         18          2012  101759490   53262945.0            NaN
26                                     THE APPARITION         18          2012   10637281    4936819.0            NaN
27       CHILDREN OF THE CORN II: THE FINAL SACRIFICE         18          1993    6953340    6953340.0            NaN
28                               I SPIT ON YOUR GRAVE         19          2010    1278471      93051.0            NaN
29                               I SPIT ON YOUR GRAVE         19          2013      80472        810.0            NaN
30                                       THE COVENANT         19          2006   38164784   23364784.0            NaN
31                            HALLOWEEN: RESURRECTION         19          2002   37659652   30259652.0            NaN
32                                         SPECIES II         19          1998   26817565   19217565.0            NaN
33                               I SPIT ON YOUR GRAVE         19          2015     144661          NaN            NaN
34                                  

MOVIES RANKED BY DOMESTIC BOX OFFICE

In [177]:
rankbybox = cleanmerge.sort_values(by=['Domestic'], ascending=False)
rankbybox.index = np.arange(1, len(rankbybox) + 1)
rankbybox = rankbybox[rankbybox['Domestic'] != 'nan']

In [178]:
rankbybox.head(10)

Title Rating  Runtime IMDB Score  Metascore  Release Year  Worldwide     Domestic  International
1              THE EXORCIST      R    122.0        8.1         81          1973  428214478  230347346.0            NaN
2             A QUIET PLACE  PG-13     90.0        7.5         82          2018  334876670  188024361.0            NaN
3     A QUIET PLACE PART II  PG-13     97.0        7.2         71          2021  296650356  160215764.0            NaN
4                 HALLOWEEN      R    106.0        6.5         67          2018  255416089  159366015.0            NaN
5   THE BLAIR WITCH PROJECT      R     81.0        6.5         81          1999  248300000  140539099.0            NaN
6             THE CONJURING      R    112.0        7.5         68          2013  317740900  137400141.0            NaN
7           THE CONJURING 2      R    134.0        7.3         65          2013  317740900  137400141.0            NaN
8                  THE RING  PG-13    115.0        7.1         57          2002  248218486  129094024.0            NaN
9                THE GRUDGE  PG-13     91.0        5.9         49          2004  187281115  110359362.0            NaN
10               THE GRUDGE      R     94.0        4.4         41          2004  187281115  110359362.0            NaN

MOVIES BY RATING

In [81]:
##rank by IMDB - DONE - rankbyimdb

##rank by metascore - DONE - rankmeta

##rank by box office (domestic) - DONE - rankbybox

#earnings/critical scores by rating?

##sort by decade?

##normalize scores - imdb * 10 vs MS

##films that consistently rank high on critical/audience scores collected in one visual

In [82]:
#wwbo = wwbo.drop(594)

In [84]:
rankbyimdb.to_csv('rankbyimdb.csv')

In [85]:
rankbyimdbbottom = cleanmerge.sort_values(by=['IMDB Score'], ascending=True)
rankbyimdbbottom.index = np.arange(1, len(rankbyimdbbottom) + 1)

In [86]:
rankbyimdbbottom = rankbyimdbbottom.drop(4)
rankbyimdbbottom = rankbyimdbbottom.drop(5)

In [87]:
rankbyimdbbottom

Title     Rating Runtime IMDB Score Metascore Release Year    Worldwide       Domestic  International
1                                   HOUSE OF THE DEAD          R    90.0        2.1        15         2003   13,860,078   10,199,354.0    3,660,724.0
2                                   ALONE IN THE DARK          R    96.0        2.4         9         2005   10,588,079    5,178,569.0    5,409,510.0
3            THE HUMAN CENTIPEDE III (FINAL SEQUENCE)  Not Rated   102.0        2.8         5         2015       18,976       14,562.0        4,414.0
6                                         SLENDER MAN      PG-13    93.0        3.2        30         2018   51,945,949   30,564,825.0   21,381,124.0
7                                            DELIRIUM      TV-MA    86.0        3.3        27         2018          878            nan          878.0
8        TEXAS CHAINSAW MASSACRE: THE NEXT GENERATION          R    87.0        3.3        50         1995       94,558       94,558.0            nan
9                                          FEARDOTCOM          R   101.0        3.4        16         2002   13,289,290   13,208,023.0       81,267.0
10                                    BLACK CHRISTMAS      PG-13    92.0        3.5        49         2006   16,235,738   16,235,738.0            nan
11                                    BLACK CHRISTMAS      PG-13    92.0        3.5        49         2019   18,526,087   10,429,730.0    8,096,357.0
12                                          SACRILEGE  NO RATING    83.0        3.5        33         2020       13,548            nan       13,548.0
13                                           CREATURE          R    93.0        3.6        31         2011      533,235      508,714.0       24,521.0
14                                           THRILLER      TV-MA    87.0        3.6        28         2019        1,188            nan        1,188.0
15                                           JAWS 3-D         PG    99.0        3.7        27         1983   42,245,180   42,245,180.0            nan
16                                          ABANDONED      PG-13   102.0        3.7        38         2022       96,761       96,761.0            nan
17                                     THE WICKER MAN      PG-13   102.0        3.7        36         2006   37,721,827   24,413,467.0   13,308,360.0
18                                        CABIN FEVER          R    99.0        3.7        14         2003   30,351,664   21,158,188.0    9,193,476.0
19              THE HUMAN CENTIPEDE 2 (FULL SEQUENCE)  Not Rated    91.0        3.8        17         2015       18,976       14,562.0        4,414.0
20                           EXORCIST II: THE HERETIC          R   117.0        3.8        39         1977   25,011,000   25,011,000.0            nan
21                                        PIRANHA 3DD          R    83.0        3.8        24         2012    6,530,796      370,904.0    6,159,892.0
22                                        PIRANHA 3DD          R    83.0        3.8        24         2010   83,660,160   25,003,155.0   58,657,005.0
23                            HALLOWEEN: RESURRECTION          R    94.0        3.9        19         2002   37,659,652   30,259,652.0    7,400,000.0
24                      THE HAUNTING OF MOLLY HARTLEY      PG-13    85.0        3.9        28         2008   15,318,257   13,442,412.0    1,875,845.0
25                                         PROM NIGHT      PG-13    88.0        3.9        17         2008   57,193,655   43,869,350.0   13,324,305.0
26                           THE DISAPPOINTMENTS ROOM          R    91.0        3.9        31         2016    3,503,761    2,423,467.0    1,080,294.0
27                                        THE TURNING      PG-13    94.0        3.9        35         2020   18,460,739   15,472,775.0    2,987,964.0
28                                     SOUL SURVIVORS      PG-13    84.0        3.9        20         2001    4,288,246    3,100,650.0    1,187,596.

In [88]:
rankbyimdbbottom = rankbyimdbbottom.drop(10)
rankbyimdbbottom = rankbyimdbbottom.drop(11)

In [89]:
rankbyimdbbottom.index = np.arange(1, len(rankbyimdbbottom) + 1)
rankbyimdbbottom = rankbyimdbbottom.head(10)

In [132]:
rankbyimdbbottom

Title     Rating Runtime IMDB Score Metascore Release Year      Domestic International
1                              HOUSE OF THE DEAD          R    90.0        2.1        15         2003  10,199,354.0   3,660,724.0
2                              ALONE IN THE DARK          R    96.0        2.4         9         2005   5,178,569.0   5,409,510.0
3       THE HUMAN CENTIPEDE III (FINAL SEQUENCE)  Not Rated   102.0        2.8         5         2015      14,562.0       4,414.0
4                                    SLENDER MAN      PG-13    93.0        3.2        30         2018  30,564,825.0  21,381,124.0
5                                       DELIRIUM      TV-MA    86.0        3.3        27         2018           nan         878.0
6   TEXAS CHAINSAW MASSACRE: THE NEXT GENERATION          R    87.0        3.3        50         1995      94,558.0           nan
7                                     FEARDOTCOM          R   101.0        3.4        16         2002  13,208,023.0      81,267.0
8                                      SACRILEGE  NO RATING    83.0        3.5        33         2020           nan      13,548.0
9                                       CREATURE          R    93.0        3.6        31         2011     508,714.0      24,521.0
10                                      THRILLER      TV-MA    87.0        3.6        28         2019           nan       1,188.0

In [158]:
rankbyimdbbottom = rankbyimdbbottom.drop('Rating', axis=1)
rankbyimdbbottom = rankbyimdbbottom.drop('Runtime', axis=1)

In [164]:
rankbyimdbbottom = rankbyimdbbottom.drop('Metascore', axis=1)

In [165]:
rankbyimdbbottom

Title IMDB Score Release Year      Domestic International
1                              HOUSE OF THE DEAD        2.1         2003  10,199,354.0   3,660,724.0
2                              ALONE IN THE DARK        2.4         2005   5,178,569.0   5,409,510.0
3       THE HUMAN CENTIPEDE III (FINAL SEQUENCE)        2.8         2015      14,562.0       4,414.0
4                                    SLENDER MAN        3.2         2018  30,564,825.0  21,381,124.0
5                                       DELIRIUM        3.3         2018           nan         878.0
6   TEXAS CHAINSAW MASSACRE: THE NEXT GENERATION        3.3         1995      94,558.0           nan
7                                     FEARDOTCOM        3.4         2002  13,208,023.0      81,267.0
8                                      SACRILEGE        3.5         2020           nan      13,548.0
9                                       CREATURE        3.6         2011     508,714.0      24,521.0
10                                      THRILLER        3.6         2019           nan       1,188.0

In [91]:
rankbyimdbbottom.to_csv('rankbyimdbbottom.csv')

In [100]:
cleanmerge['Worldwide'] = cleanmerge['Worldwide'].replace(',', '', regex=True)
cleanmerge['Worldwide'] = cleanmerge['Worldwide'].apply(pd.to_numeric)

C:\Users\rober\AppData\Local\Temp\ipykernel_23112\2139490508.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Worldwide'] = cleanmerge['Worldwide'].replace(',', '', regex=True)
C:\Users\rober\AppData\Local\Temp\ipykernel_23112\2139490508.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Worldwide'] = cleanmerge['Worldwide'].apply(pd.to_numeric)


In [110]:
cleanmerge['Domestic'] = cleanmerge['Domestic'].replace(',', '', regex=True)
cleanmerge['Domestic'] = pd.to_numeric(cleanmerge['Domestic'], errors='coerce')

C:\Users\rober\AppData\Local\Temp\ipykernel_23112\2429497775.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Domestic'] = cleanmerge['Domestic'].replace(',', '', regex=True)
C:\Users\rober\AppData\Local\Temp\ipykernel_23112\2429497775.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Domestic'] = pd.to_numeric(cleanmerge['Domestic'], errors='coerce')


In [112]:
cleanmerge['Runtime'] = pd.to_numeric(cleanmerge['Runtime'], errors='coerce')

C:\Users\rober\AppData\Local\Temp\ipykernel_23112\1284636241.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Runtime'] = pd.to_numeric(cleanmerge['Runtime'], errors='coerce')


In [114]:
cleanmerge['Metascore'] = pd.to_numeric(cleanmerge['Metascore'], errors='coerce')

C:\Users\rober\AppData\Local\Temp\ipykernel_23112\920940606.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Metascore'] = pd.to_numeric(cleanmerge['Metascore'], errors='coerce')


In [116]:
cleanmerge['Release Year'] = pd.to_numeric(cleanmerge['Release Year'], errors='coerce')

C:\Users\rober\AppData\Local\Temp\ipykernel_23112\184968798.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['Release Year'] = pd.to_numeric(cleanmerge['Release Year'], errors='coerce')


In [118]:
cleanmerge['International'] = pd.to_numeric(cleanmerge['International'], errors='coerce')

C:\Users\rober\AppData\Local\Temp\ipykernel_23112\2835438518.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleanmerge['International'] = pd.to_numeric(cleanmerge['International'], errors='coerce')


In [ ]:
cleanmerge.dtypes